In [1]:
import http.client
import json
import csv


In [6]:


class Graph:

    # Do not modify
    def __init__(self, with_nodes_file=None, with_edges_file=None):
        """
        option 1:  init as an empty graph and add nodes
        option 2: init by specifying a path to nodes & edges files
        """
        self.nodes = []
        self.edges = []
        if with_nodes_file and with_edges_file:
            nodes_CSV = csv.reader(open(with_nodes_file))
            nodes_CSV = list(nodes_CSV)[1:]
            self.nodes = [(n[0], n[1]) for n in nodes_CSV]

            edges_CSV = csv.reader(open(with_edges_file))
            edges_CSV = list(edges_CSV)[1:]
            self.edges = [(e[0], e[1]) for e in edges_CSV]


    def add_node(self, id: str, name: str) -> None:
        """
        add a tuple (id, name) representing a node to self.nodes if it does not already exist
        The graph should not contain any duplicate nodes
        """
        if (id, name) not in self.nodes:
            self.nodes.append((id, name))

        # return NotImplemented


    def add_edge(self, source: str, target: str) -> None:
        """
        Add an edge between two nodes if it does not already exist.
        An edge is represented by a tuple containing two strings: e.g.: ('source', 'target').
        Where 'source' is the id of the source node and 'target' is the id of the target node
        e.g., for two nodes with ids 'a' and 'b' respectively, add the tuple ('a', 'b') to self.edges
        """
        current_edge = (source, target)
        current_edge_inverted = (target, source)
        if (source != target) and (current_edge not in self.edges) and (current_edge_inverted not in self.edges):
            self.edges.append(current_edge)

        # return NotImplemented


    def total_nodes(self) -> int:
        """
        Returns an integer value for the total number of nodes in the graph
        """
        return len(self.nodes)
        # return NotImplemented

    def total_edges(self) -> int:
        """
        Returns an integer value for the total number of edges in the graph
        """
        return len(self.edges)
        # return NotImplemented

    def non_leaf_nodes(self):
        nodes_degrees = {}
        for edge in self.edges:
            for idx in edge:
                if idx in nodes_degrees:
                    nodes_degrees[idx] += 1
                else:
                    nodes_degrees[idx] = 1
    
        non_leaf_nodes = dict((k, v) for k, v in nodes_degrees.items() if v > 1)
        return len(non_leaf_nodes)



    def max_degree_nodes(self) -> dict:
        """
        Return the node(s) with the highest degree
        Return multiple nodes in the event of a tie
        Format is a dict where the key is the node_id and the value is an integer for the node degree
        e.g. {'a': 8}
        or {'a': 22, 'b': 22}
        """

        max_degree_nodes = {}

        for edge in self.edges:
            for idx in edge:
                if idx in max_degree_nodes:
                    max_degree_nodes[idx] += 1
                else:
                    max_degree_nodes[idx] = 1

        v = list(max_degree_nodes.values())
        k = list(max_degree_nodes.keys())
        max_nodes = {k[v.index(max(v))]: max(v)}
        print(max_nodes)
        return max_nodes

    def print_nodes(self):
        """
        No further implementation required
        May be used for de-bugging if necessary
        """
        print(self.nodes)

    def print_edges(self):
        """
        No further implementation required
        May be used for de-bugging if necessary
        """
        print(self.edges)

    # Do not modify
    def write_edges_file(self, path="edges.csv")->None:
        """
        write all edges out as .csv
        :param path: string
        :return: None
        """
        edges_path = path
        edges_file = open(edges_path, 'w', encoding='utf-8')

        edges_file.write("source" + "," + "target" + "\n")

        for e in self.edges:
            edges_file.write(e[0] + "," + e[1] + "\n")

        edges_file.close()
        print("finished writing edges to csv")

    # Do not modify
    def write_nodes_file(self, path="nodes.csv")->None:
        """
        write all nodes out as .csv
        :param path: string
        :return: None
        """
        nodes_path = path
        nodes_file = open(nodes_path, 'w', encoding='utf-8')

        nodes_file.write("id,name" + "\n")
        for n in self.nodes:
            nodes_file.write(n[0] + "," + n[1] + "\n")
        nodes_file.close()
        print("finished writing nodes to csv")


In [7]:

class TMDBAPIUtils:

    # Do not modify
    def __init__(self, api_key:str):
        self.api_key=api_key

    def get_movie_cast(self, movie_id:str, limit:int=None, exclude_ids:list=None) -> list:
        """
        Get the movie cast for a given movie id, with optional parameters to exclude an cast member
        from being returned and/or to limit the number of returned cast members
        documentation url: https://developers.themoviedb.org/3/movies/get-movie-credits

        :param integer movie_id: a movie_id
        :param integer limit: maximum number of returned cast members by their 'order' attribute
            e.g., limit=5 will attempt to return the 5 cast members having 'order' attribute values between 0-4
            If after excluding, there are fewer cast members than the specified limit, then return the remaining members (excluding the ones whose order values are outside the limit range). 
            If cast members with 'order' attribute in the specified limit range have been excluded, do not include more cast members to reach the limit.
            If after excluding, the limit is not specified, then return all remaining cast members."
            e.g., if limit=5 and the actor whose id corresponds to cast member with order=1 is to be excluded,
            return cast members with order values [0, 2, 3, 4], not [0, 2, 3, 4, 5]
        :param list exclude_ids: a list of ints containing ids (not cast_ids) of cast members  that should be excluded from the returned result
            e.g., if exclude_ids are [353, 455] then exclude these from any result.
        :rtype: list
            return a list of dicts, one dict per cast member with the following structure:
                [{'id': '97909' # the id of the cast member
                'character': 'John Doe' # the name of the character played
                'credit_id': '52fe4249c3a36847f8012927' # id of the credit, ...}, ... ]
                Note that this is an example of the structure of the list and some of the fields returned by the API.
                The result of the API call will include many more fields for each cast member.

        Important: the exclude_ids processing should occur prior to limiting output.
        """

        connection = http.client.HTTPSConnection('api.themoviedb.org')
        connection.request("GET", "/3/movie/{0}/credits?api_key={1}&language=en-US".format(movie_id, self.api_key))
        response = connection.getresponse()
        if response.status == 200:
            data = response.read()
            decoded_data = json.loads(data.decode('UTF-8'))
            cast = decoded_data['cast']
            if exclude_ids is not None:
                cast = [i for i in cast if i['id'] not in exclude_ids]
                print(cast)
            if limit is not None:
                cast = [i for i in cast if i['order'] < limit]
                print(cast)
            for c in cast:
                c['name'] = c['name'].replace(',', '')
            return cast
        else:
            print(response.status.__str__())
            return None

    def get_movie_credits_for_person(self, person_id:str, vote_avg_threshold:float=None)->list:
        """
        Using the TMDb API, get the movie credits for a person serving in a cast role
        documentation url: https://developers.themoviedb.org/3/people/get-person-movie-credits

        :param string person_id: the id of a person
        :param vote_avg_threshold: optional parameter to return the movie credit if it is >=
            the specified threshold.
            e.g., if the vote_avg_threshold is 5.0, then only return credits with a vote_avg >= 5.0
        :rtype: list
            return a list of dicts, one dict per movie credit with the following structure:
                [{'id': '97909' # the id of the movie credit
                'title': 'Long, Stock and Two Smoking Barrels' # the title (not original title) of the credit
                'vote_avg': 5.0 # the float value of the vote average value for the credit}, ... ]
        """

        connection = http.client.HTTPSConnection('api.themoviedb.org')
        connection.request("GET", "/3/person/{0}/movie_credits?api_key={1}&language=en-US".format(person_id, self.api_key))
        response = connection.getresponse()
        if response.status == 200:
            data = response.read()
            decoded_data = json.loads(data.decode('UTF-8'))
            raw_credits = decoded_data['cast']
            if vote_avg_threshold is not None:
                filtered_credits = [{"id":idx["id"], "title":idx["title"], "vote_avg":idx["vote_average"]} for idx in raw_credits if idx["vote_average"] >= vote_avg_threshold]
                print(filtered_credits)
                return filtered_credits
            else:
                unfiltered_credits = [{"id":idx["id"], "title":idx["title"], "vote_avg":idx["vote_average"]} for idx in raw_credits]
                print(unfiltered_credits)
                return unfiltered_credits
        else:
            print("ERROR: " + response.status.__str__())
            return None



In [8]:

def return_name()->str:
    """
    Return a string containing your GT Username
    e.g., gburdell3
    Do not return your 9 digit GTId
    """
    return "kobrien43"


def return_argo_lite_snapshot()->str:
    """
    Return the shared URL of your published graph in Argo-Lite
    """
    return "https://poloclub.github.io/argo-graph-lite/#1ac32aec-ba9f-4693-83e1-cd4a7e81fb93"


In [9]:

if __name__ == "__main__":

    # init graph object with a single node representing laurence fishburne
    graph = Graph()
    graph.add_node(id='2975', name='Laurence Fishburne')

    # build base graph
    # find all laurence fishburne's movie credits with a vote average >= 8.0
    tmdb_api_utils = TMDBAPIUtils(api_key='25166b54e76c7ad3aaa306abdfecb190')
    movie_credits = tmdb_api_utils.get_movie_credits_for_person(person_id='2975', vote_avg_threshold=8.0)
    print(len(movie_credits))
    print(movie_credits)

    # for each movie credit get movie cast members having and order value between 0-2 (3 0-base)
    for movie in movie_credits:
        movie_cast = tmdb_api_utils.get_movie_cast(movie_id=movie['id'], limit=3)
        for cast_member in movie_cast:
            graph.add_node(str(cast_member['id']), cast_member['name'])
            graph.add_edge(source='2975', target=str(cast_member['id']))

    for i in range(2):
        if i == 0:
            current_nodes = graph.nodes[1:]
        else:
            current_nodes = [i for i in graph.nodes if i not in current_nodes]

        for node in current_nodes:
            cast = tmdb_api_utils.get_movie_credits_for_person(person_id=node[0], vote_avg_threshold=8.0)
            for movie in cast:
                actors = tmdb_api_utils.get_movie_cast(movie_id=movie['id'], limit=3)
                for actor in actors:
                    graph.add_node(str(actor['id']), actor['name'])
                    graph.add_edge(str(node[0]), str(actor['id']))



    # tmdb_api_utils.get_movie_cast(movie_id='100', limit=3, exclude_ids=[973, 974])
    # tmdb_api_utils.get_movie_credits_for_person(person_id="9709", vote_avg_threshold=5.0)

    # call functions or place code here to build graph (graph building code not graded)
    # Suggestion: code should contain steps outlined above in BUILD CO-ACTOR NETWORK

    print("Edges: " + str(graph.total_edges()))
    print("Nodes: " + str(graph.total_nodes()))

    graph.write_edges_file()
    graph.write_nodes_file()

    # If you have already built & written out your graph, you could read in your nodes & edges files
    # to perform testing on your graph.
    graph = Graph(with_edges_file="edges.csv", with_nodes_file="nodes.csv")

    #get non-leaf nodes
    non_leaf = graph.non_leaf_nodes()
    print(non_leaf - 10)
    print("DONE")


[{'id': 603, 'title': 'The Matrix', 'vote_avg': 8.207}, {'id': 28, 'title': 'Apocalypse Now', 'vote_avg': 8.282}, {'id': 201335, 'title': 'King: Man of Peace in a Time of War', 'vote_avg': 8.5}, {'id': 963164, 'title': 'black-ish: A Celebration – An ABC News Special', 'vote_avg': 10.0}]
4
[{'id': 603, 'title': 'The Matrix', 'vote_avg': 8.207}, {'id': 28, 'title': 'Apocalypse Now', 'vote_avg': 8.282}, {'id': 201335, 'title': 'King: Man of Peace in a Time of War', 'vote_avg': 8.5}, {'id': 963164, 'title': 'black-ish: A Celebration – An ABC News Special', 'vote_avg': 10.0}]
[{'adult': False, 'gender': 2, 'id': 6384, 'known_for_department': 'Acting', 'name': 'Keanu Reeves', 'original_name': 'Keanu Reeves', 'popularity': 61.33, 'profile_path': '/4D0PpNI0kmP58hgrwGC3wCjxhnm.jpg', 'cast_id': 34, 'character': 'Thomas A. Anderson / Neo', 'credit_id': '52fe425bc3a36847f80181c1', 'order': 0}, {'adult': False, 'gender': 2, 'id': 2975, 'known_for_department': 'Acting', 'name': 'Laurence Fishburne',

[{'adult': False, 'gender': 2, 'id': 1776, 'known_for_department': 'Directing', 'name': 'Francis Ford Coppola', 'original_name': 'Francis Ford Coppola', 'popularity': 10.003, 'profile_path': '/3Pblihd6KjXliie9vj4iQJwbNPU.jpg', 'cast_id': 2, 'character': 'Self', 'credit_id': '5fd4dbd72cefc2003f1d7f99', 'order': 0}, {'adult': False, 'gender': 2, 'id': 38803, 'known_for_department': 'Writing', 'name': 'Roman Coppola', 'original_name': 'Roman Coppola', 'popularity': 5.809, 'profile_path': '/rKamKkx78qjZTfvqi2OWCo5p6x5.jpg', 'cast_id': 3, 'character': 'Self', 'credit_id': '5fd4dc095ed962003fe03bf9', 'order': 1}, {'adult': False, 'gender': 2, 'id': 64, 'known_for_department': 'Acting', 'name': 'Gary Oldman', 'original_name': 'Gary Oldman', 'popularity': 331.472, 'profile_path': '/2v9FVVBUrrkW2m3QOcYkuhq9A6o.jpg', 'cast_id': 4, 'character': 'Self (archive footage)', 'credit_id': '5fd4dc26d48cee003a725932', 'order': 2}]
[{'adult': False, 'gender': 2, 'id': 20215, 'known_for_department': 'Actin

[{'adult': False, 'gender': 2, 'id': 8349, 'known_for_department': 'Acting', 'name': 'Martin Sheen', 'original_name': 'Martin Sheen', 'popularity': 30.857, 'profile_path': '/5W4OuI6evOYyPc3pUnKAEnpLtX3.jpg', 'cast_id': 1, 'character': 'Narrator', 'credit_id': '5d2df7496a300b000fa4a3a6', 'order': 0}]
[{'adult': False, 'gender': 2, 'id': 8349, 'known_for_department': 'Acting', 'name': 'Martin Sheen', 'original_name': 'Martin Sheen', 'popularity': 30.857, 'profile_path': '/5W4OuI6evOYyPc3pUnKAEnpLtX3.jpg', 'cast_id': 1, 'character': 'Self', 'credit_id': '5dfe65f565686e001892f4aa', 'order': 0}, {'adult': False, 'gender': 1, 'id': 5606, 'known_for_department': 'Acting', 'name': 'Sissy Spacek', 'original_name': 'Sissy Spacek', 'popularity': 20.63, 'profile_path': '/xAxenjxjLNQFq4v1ccS2to3Mnoq.jpg', 'cast_id': 2, 'character': 'Self', 'credit_id': '5dfe65fdd1a893001487c897', 'order': 1}, {'adult': False, 'gender': 2, 'id': 5632, 'known_for_department': 'Art', 'name': 'Jack Fisk', 'original_nam

[{'adult': False, 'gender': 2, 'id': 2641, 'known_for_department': 'Acting', 'name': 'Martin Landau', 'original_name': 'Martin Landau', 'popularity': 21.622, 'profile_path': '/dznOAZPpAyXu7PfCz5obbJ2YzsJ.jpg', 'cast_id': 3, 'character': 'Roy Tilden', 'credit_id': '56a56cc492514154f00063b1', 'order': 0}, {'adult': False, 'gender': 2, 'id': 92029, 'known_for_department': 'Acting', 'name': 'Gabriel Bologna', 'original_name': 'Gabriel Bologna', 'popularity': 2.09, 'profile_path': None, 'cast_id': 5, 'character': 'David Brochman', 'credit_id': '56a56d49925141720700870d', 'order': 1}, {'adult': False, 'gender': 1, 'id': 218506, 'known_for_department': 'Acting', 'name': 'Gretchen Becker', 'original_name': 'Gretchen Becker', 'popularity': 1.53, 'profile_path': None, 'cast_id': 20, 'character': 'Doris', 'credit_id': '61ac9976596a91008dac7300', 'order': 2}]
[{'adult': False, 'gender': 0, 'id': 2098136, 'known_for_department': 'Acting', 'name': 'Brian Becker', 'original_name': 'Brian Becker', 'po

[{'adult': False, 'gender': 1, 'id': 180659, 'known_for_department': 'Acting', 'name': 'Rosa Parks', 'original_name': 'Rosa Parks', 'popularity': 0.716, 'profile_path': '/pEc0ZvL4jdKDc7g89Nd2GzPhYEL.jpg', 'cast_id': 2, 'character': '', 'credit_id': '52fe4efac3a36847f82b4f25', 'order': 0}, {'adult': False, 'gender': 2, 'id': 1107983, 'known_for_department': 'Acting', 'name': 'Martin Luther King Jr.', 'original_name': 'Martin Luther King Jr.', 'popularity': 6.588, 'profile_path': '/5AYILU60HVNMWmhDEhFtnJVv31O.jpg', 'cast_id': 3, 'character': '', 'credit_id': '52fe4efac3a36847f82b4f29', 'order': 1}, {'adult': False, 'gender': 1, 'id': 1280183, 'known_for_department': 'Acting', 'name': 'Coretta Scott King', 'original_name': 'Coretta Scott King', 'popularity': 0.696, 'profile_path': '/uMW0Bkp76fst7aSqlUqGd0B9lWA.jpg', 'cast_id': 4, 'character': '', 'credit_id': '52fe4efac3a36847f82b4f2d', 'order': 2}]
[{'adult': False, 'gender': 2, 'id': 1165240, 'known_for_department': 'Acting', 'name': 'J

...

[{'adult': False, 'gender': 1, 'id': 5823, 'known_for_department': 'Acting', 'name': 'Julie Andrews', 'original_name': 'Julie Andrews', 'popularity': 23.334, 'profile_path': '/kTXM2KfsXh2vSav0s9vaDKfs4lR.jpg', 'cast_id': 0, 'character': 'Self - Host', 'credit_id': '5b71f72c9251414064194470', 'order': 0}, {'adult': False, 'gender': 1, 'id': 80866, 'known_for_department': 'Acting', 'name': 'Nell Carter', 'original_name': 'Nell Carter', 'popularity': 7.621, 'profile_path': '/wyTkvDZQ8bW1ostuZRMICXaZxzV.jpg', 'cast_id': 8, 'character': 'Self - Performer', 'credit_id': '5b71f7eb0e0a267ef41a0075', 'order': 1}, {'adult': False, 'gender': 1, 'id': 40063, 'known_for_department': 'Acting', 'name': 'Lea DeLaria', 'original_name': 'Lea DeLaria', 'popularity': 7.033, 'profile_path': '/PNq2MS2Wc9SgQT82L6q2vIOgl4.jpg', 'cast_id': 9, 'character': 'Self - Performer', 'credit_id': '5b71f7f59251414056166da2', 'order': 2}]
[{'adult': False, 'gender': 1, 'id': 5823, 'known_for_department': 'Acting', 'name'

[{'adult': False, 'gender': 2, 'id': 3223, 'known_for_department': 'Acting', 'name': 'Robert Downey Jr.', 'original_name': 'Robert Downey Jr.', 'popularity': 57.549, 'profile_path': '/im9SAqJPZKEbVZGmjXuLI4O7RvM.jpg', 'cast_id': 493, 'character': 'Tony Stark / Iron Man', 'credit_id': '5e85cd735294e700134abf26', 'order': 0}, {'adult': False, 'gender': 2, 'id': 16828, 'known_for_department': 'Acting', 'name': 'Chris Evans', 'original_name': 'Chris Evans', 'popularity': 54.789, 'profile_path': '/3bOGNsHlrswhyW79uvIHH1V43JI.jpg', 'cast_id': 494, 'character': 'Steve Rogers / Captain America', 'credit_id': '5e85cd84691cd50018593984', 'order': 1}, {'adult': False, 'gender': 2, 'id': 103, 'known_for_department': 'Acting', 'name': 'Mark Ruffalo', 'original_name': 'Mark Ruffalo', 'popularity': 24.975, 'profile_path': '/z3dvKqMNDQWk3QLxzumloQVR0pv.jpg', 'cast_id': 594, 'character': 'Bruce Banner / Hulk', 'credit_id': '5e85e1ab0c3ec800135aabd6', 'order': 2}]
[{'id': 77230, 'title': 'Adele Live at 

[{'adult': False, 'gender': 0, 'id': 3889844, 'known_for_department': 'Acting', 'name': 'Haizel Adofo', 'original_name': 'Haizel Adofo', 'popularity': 0.6, 'profile_path': None, 'cast_id': 9, 'character': '(voice)', 'credit_id': '63d0b931e72fe800b2045213', 'order': 0}, {'adult': False, 'gender': 1, 'id': 13309, 'known_for_department': 'Acting', 'name': 'Oprah Winfrey', 'original_name': 'Oprah Winfrey', 'popularity': 10.192, 'profile_path': '/nNpYieaDLxKZWw2FY9wsDkjwURu.jpg', 'cast_id': 3, 'character': 'Self (voice) (archive footage) (uncredited)', 'credit_id': '62263b8a7c6de300644f8367', 'order': 1}]
[{'adult': False, 'gender': 2, 'id': 113461, 'known_for_department': 'Acting', 'name': 'John Legend', 'original_name': 'John Legend', 'popularity': 11.799, 'profile_path': '/cCv0YBy2YFFWp9h3kvNPmwWwrCD.jpg', 'cast_id': 2, 'character': 'Crow (voice)', 'credit_id': '62c3b8f60443c9005abb0392', 'order': 0}, {'adult': False, 'gender': 1, 'id': 206444, 'known_for_department': 'Acting', 'name': '

[{'adult': False, 'gender': 1, 'id': 66620, 'known_for_department': 'Acting', 'name': 'Angela Merkel', 'original_name': 'Angela Merkel', 'popularity': 3.096, 'profile_path': '/fjlqfSwhiRpwgsEtzJ8X004NpBw.jpg', 'cast_id': 1, 'character': 'Self', 'credit_id': '62000af44b9bae008c0fa65c', 'order': 0}, {'adult': False, 'gender': 2, 'id': 102786, 'known_for_department': 'Acting', 'name': 'Barack Obama', 'original_name': 'Barack Obama', 'popularity': 11.509, 'profile_path': '/reEkbvLlNknpCo2I37Vim6XpqGu.jpg', 'cast_id': 2, 'character': 'Self (archive footage)', 'credit_id': '62000b0155b0c0001b6cfb46', 'order': 1}, {'adult': False, 'gender': 1, 'id': 2134341, 'known_for_department': 'Acting', 'name': 'Theresa May', 'original_name': 'Theresa May', 'popularity': 4.418, 'profile_path': '/wJWj09yNksHaRBzlAkF1mmsScAA.jpg', 'cast_id': 3, 'character': 'Self (archive footage)', 'credit_id': '62000b0c55b0c0006796fa4d', 'order': 2}]
[{'adult': False, 'gender': 0, 'id': 3089883, 'known_for_department': '

[{'adult': False, 'gender': 0, 'id': 2169865, 'known_for_department': 'Acting', 'name': 'Birgitta Assheuer', 'original_name': 'Birgitta Assheuer', 'popularity': 0.6, 'profile_path': None, 'cast_id': 62, 'character': 'Self - Narrator (voice)', 'credit_id': '5ff1b34bd2f5b5003d2d6e7c', 'order': 0}, {'adult': False, 'gender': 1, 'id': 2920376, 'known_for_department': 'Acting', 'name': 'Îlham Ahmed', 'original_name': 'Îlham Ahmed', 'popularity': 0.6, 'profile_path': None, 'cast_id': 4, 'character': 'Self - Politician', 'credit_id': '5ff08e54cd2f0f003e0427dd', 'order': 1}, {'adult': False, 'gender': 2, 'id': 2920377, 'known_for_department': 'Acting', 'name': 'Zaher al-Saket', 'original_name': 'Zaher al-Saket', 'popularity': 1.38, 'profile_path': None, 'cast_id': 5, 'character': 'Self - Former Syrian Military Gen.', 'credit_id': '5ff08e62fad8e9003c791b34', 'order': 2}]
[{'adult': False, 'gender': 2, 'id': 13611, 'known_for_department': 'Acting', 'name': 'Jack White', 'original_name': 'Jack Wh